## using pandas


In [2]:
import pandas as pd
import numpy as np
import os
import json
## column : file no 1~25

# array 4X4
# for i in range(rows):
#     for j in range(cols):
#         object_array[i,j] = np.zeros((4,4))


data = np.zeros((20,25))



## row : bottle_0, bottle_25 ... gt 0 25 --> 10 rows. 

categories = ['bottle2', 'lightbulb', 'lighter', 'eyeglasses', 'magnifying_glass', 'spray']

category = categories[3]
fill_rate = ['100', '75', '50', '25', '0']

columns = [f'file_{i}' for i in range(1,26)]





## Get transformation file 

In [3]:
## Tmatrix FOlder access -> save in pandas
robust_no = ['0','2','3','6']
new_row_names = []
# 결과를 저장할 딕셔너리를 카테고리별로 초기화합니다.
grouped_files = {fill: [] for fill in fill_rate}

for no in robust_no:
    
    ## get txt file

    ########################  We got the txt file list#################
    for fills in fill_rate:
        
        if no =='0':
            name = "ICP"
        elif no == '2':
            name = "FAST ICP"
        elif no =='3':
            name = "Robust ICP"
        else:
            name = "Sparse ICP"

        new_row_names.append(f"{category}_{fills}_{name}")

df = pd.DataFrame(data, index=new_row_names, columns=columns, dtype=object)
# 2. df.index에 새로운 이름 리스트를 바로 할당 object for array 4x4

df.info

<bound method DataFrame.info of                           file_1 file_2 file_3 file_4 file_5 file_6 file_7  \
eyeglasses_100_ICP           0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_75_ICP            0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_50_ICP            0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_25_ICP            0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_0_ICP             0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_100_FAST ICP      0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_75_FAST ICP       0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_50_FAST ICP       0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_25_FAST ICP       0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_0_FAST ICP        0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_100_Robust ICP    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
eyeglasses_75_Robust ICP     0.0

## RMSE function

In [4]:
def RMSE(T_star, T):
    diff = T_star - T
    sq_norms = np.sum(diff**2, axis =1)

    r = np.sqrt(np.mean(sq_norms))

    return r

##  get T from Result Txt file
def get_T(file_path):

    try:
        with open(file_path, 'r') as f:
            T_matrix = np.loadtxt(file_path)
        return T_matrix
    except FileNotFoundError:
    # try 블록에서 FileNotFoundError가 발생했을 때만 이 코드가 실행됩니다.
        print(f"⚠️ 경고: '{file_path}' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.")
        return None  # 파일이 없으므로 None을 반환




def get_GT_T(file_path,data_name):

    try:
        with open(file_path, 'r') as f:
            loaded_data = json.load(f)
        noisy_data = loaded_data[data_name]
        T_matrix = noisy_data['matrix_world']
        np.array(T_matrix)
        return T_matrix

    except FileNotFoundError:
    # try 블록에서 FileNotFoundError가 발생했을 때만 이 코드가 실행됩니다.
        print(f"⚠️ 경고: '{file_path}' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.")
        return None  # 파일이 없으므로 None을 반환

    except KeyError as e:
    # try 블록에서 KeyError가 발생했을 때 실행됩니다. (e.g., 'matrix_world' 키가 없음)
        print(f"⚠️ 경고: 파일 '{os.path.basename(file_path)}' 안에 필요한 키({e})가 없습니다.")
        return None
    
   

def compute_RMSE(gt_files):
    
    robust_no = ['0','2','3','6']
    
    for no in robust_no:
        if no =='0':
            name = "ICP"
        elif no == '2':
            name = "FAST ICP"
        elif no =='3':
            name = "Robust ICP"
        else:
            name = "Sparse ICP"

        for key, value_list in gt_files.items():
            rmse = []
            np.array(rmse)
            # get gt_T and noisy_T
            for value in value_list:
                profix = value.split('_')[1]
                gt_path = f"./gt_raw/noisy_filtered_{key}_{profix}.json"
                gt_name = f"noisy_filtered_{key}_{profix}"

                #### RESULT FOLDER PATH.
                result_path = f'./result{no}/result_{key}_{profix}.txt'
                icp_T = get_T(result_path)
                gt_T = get_GT_T(gt_path,gt_name)
                
            

                if (gt_T is None or icp_T is None):
                    df.loc[f'{category}_{key}_{name}',f'file_{profix}'] = 0.0

                else:
                    ## conpute rmse
                    r = RMSE(gt_T, icp_T)
                
                    df.loc[f'{category}_{key}_{name}',f'file_{profix}'] = r


noisy_T = get_T("./result3/result_3_100_1.txt")
gt_T = get_GT_T("./gt/noisy_filtered_100_1.json","noisy_filtered_100_1")



⚠️ 경고: './result3/result_3_100_1.txt' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.


## Bring GT

In [5]:
json_path = "ply_files.json"
try: 
    with open(json_path, "r", encoding="utf-8") as f:
        gt_files = json.load(f)
except FileNotFoundError:
    print(f"오류: '{json_path}' 파일을 찾을 수 없습니다. 먼저 파일 분류 코드를 실행해 주세요.")
    exit() # 파일이 없으면 프로그램 종료



### get 



compute_RMSE(gt_files)

##get mean value
df['mean_Val'] = df.replace(0, np.nan).mean(axis=1)



# 모든 행/열을 전부 보여줌
pd.set_option('display.max_rows', None)       # 행 전체 출력
pd.set_option('display.max_columns', None)    # 열 전체 출력

# 각 열의 너비 제한 해제 (긴 문자열도 잘리지 않음)
pd.set_option('display.max_colwidth', None)

# 화면 너비에 따라 줄바꿈을 할지 말지
pd.set_option('display.width', None)          # None이면 자동으로 콘솔 너비를 사용
pd.set_option('display.expand_frame_repr', False)  # True면 줄바꿈 허용, False면 한 줄로 출력 시도

# 예: DataFrame 출력
print(df)
        




⚠️ 경고: './gt_raw/noisy_filtered_100_3.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
⚠️ 경고: './gt_raw/noisy_filtered_75_21.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
⚠️ 경고: './gt_raw/noisy_filtered_100_3.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
⚠️ 경고: './gt_raw/noisy_filtered_75_21.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
⚠️ 경고: './gt_raw/noisy_filtered_100_3.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
⚠️ 경고: './gt_raw/noisy_filtered_75_21.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
⚠️ 경고: './gt_raw/noisy_filtered_100_3.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
⚠️ 경고: './gt_raw/noisy_filtered_75_21.json' 경로에 파일이 없습니다. 해당 처리를 건너뜁니다.
                               file_1      file_2     file_3      file_4     file_5      file_6      file_7      file_8      file_9     file_10     file_11     file_12     file_13     file_14     file_15     file_16     file_17     file_18     file_19     file_20     file_21     file_22    file_23    file_24 file_25   mean_Val
eyeglasses_100_ICP          49.177524   49.806584        0.0  138.441225  87.915898  120.186261

/tmp/ipykernel_285739/3042233176.py:18: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df['mean_Val'] = df.replace(0, np.nan).mean(axis=1)


## GET RMSE MEAN by ICP Methods



In [6]:
df_mean = np.zeros((5,5))

## make 25 lengths array

grouping = []

for i in range(0,len(df)):
    grouping.append(i)

grouping = np.arange(len(df)) //5

print(grouping)
block_avg_df = df.groupby(grouping).mean()


ICP_Method = ['ICP', 'FAST ICP', 'FAST AND ROBUST ICP', 'SPARSE ICP']



block_avg_df.index =  ICP_Method


print(block_avg_df)

print(type(block_avg_df))




[0 0 0 0 0 1 1 1 1 1 2 2 2 2 2 3 3 3 3 3]
                        file_1     file_2     file_3     file_4     file_5     file_6     file_7      file_8      file_9     file_10     file_11    file_12    file_13    file_14    file_15    file_16    file_17     file_18    file_19    file_20    file_21    file_22    file_23    file_24 file_25   mean_Val
ICP                  85.341354  88.887397  47.023139   61.45332  54.934998  76.071344  73.060515  101.697793  114.806848   110.32652  107.365937  78.519844  63.967499  69.409217  77.080832  72.752249  96.577527  113.995142  94.781897  69.170672  23.556134   23.08887  18.382303  12.599637     0.0  84.049010
FAST ICP             92.158538   88.49653  47.021592  61.454307  54.938263  76.072606  73.062909  101.700427  114.805221  110.333409  107.197623  78.522964  63.969287  77.772819  77.082034  66.268981   96.57216  113.992938  94.776605  69.172997  23.555429  23.088534  18.366808  12.601635     0.0  84.421939
FAST AND ROBUST ICP  81.668689  84

## merge in Pandas

In [7]:
combined_df = pd.concat([df, block_avg_df], ignore_index=False)

# 모든 행/열을 전부 보여줌
pd.set_option('display.max_rows', None)       # 행 전체 출력
pd.set_option('display.max_columns', None)    # 열 전체 출력

# 각 열의 너비 제한 해제 (긴 문자열도 잘리지 않음)
pd.set_option('display.max_colwidth', None)

# 화면 너비에 따라 줄바꿈을 할지 말지
pd.set_option('display.width', None)          # None이면 자동으로 콘솔 너비를 사용
pd.set_option('display.expand_frame_repr', False)  # True면 줄바꿈 허용, False면 한 줄로 출력 시도

print(combined_df)

                               file_1      file_2     file_3      file_4     file_5      file_6      file_7      file_8      file_9     file_10     file_11     file_12     file_13     file_14     file_15     file_16     file_17     file_18     file_19     file_20     file_21     file_22    file_23    file_24 file_25   mean_Val
eyeglasses_100_ICP          49.177524   49.806584        0.0  138.441225  87.915898  120.186261   120.15116  123.894466   89.380514   73.315877   48.166215    6.039374  115.531124   77.997241   88.023412   43.083893   96.244094  117.313122  122.726607    32.79982         0.0         0.0        0.0        0.0     0.0  84.220758
eyeglasses_75_ICP           87.588102   87.952244  86.888912   44.465704  43.706854   46.803776   83.053832   86.934602  119.085669  118.664201  127.226752   89.041529   25.653662   76.212343  116.570636  110.974039  121.662971    92.39682   92.948404   45.527907         0.0         0.0        0.0        0.0     0.0  85.167948
eyeglasses_50

## Save bottle csv

In [8]:
sliced_data = combined_df.loc['ICP':'SPARSE ICP', 'mean_Val']
print(sliced_data)
combined_df.to_csv(f'{category}.csv', index=True)

ICP                    84.049010
FAST ICP               84.421939
FAST AND ROBUST ICP    78.851995
SPARSE ICP             72.398813
Name: mean_Val, dtype: float64


## Load num of dataset in each category. + save array

In [9]:


df['Counts'] = (df != 0).sum(axis=1)-1

# 모든 행/열을 전부 보여줌
pd.set_option('display.max_rows', None)       # 행 전체 출력
pd.set_option('display.max_columns', None)    # 열 전체 출력

# 각 열의 너비 제한 해제 (긴 문자열도 잘리지 않음)
pd.set_option('display.max_colwidth', None)

# 화면 너비에 따라 줄바꿈을 할지 말지
pd.set_option('display.width', None)          # None이면 자동으로 콘솔 너비를 사용
pd.set_option('display.expand_frame_repr', False)  # True면 줄바꿈 허용, False면 한 줄로 출력 시도

print(df)



sliced_data = df.loc['eyeglasses_100_ICP':'eyeglasses_0_ICP', 'Counts']
print(f"###################\n{sliced_data}")
sliced_data.to_csv(f'{category}_data_num.csv', index=True)

                               file_1      file_2     file_3      file_4     file_5      file_6      file_7      file_8      file_9     file_10     file_11     file_12     file_13     file_14     file_15     file_16     file_17     file_18     file_19     file_20     file_21     file_22    file_23    file_24 file_25   mean_Val  Counts
eyeglasses_100_ICP          49.177524   49.806584        0.0  138.441225  87.915898  120.186261   120.15116  123.894466   89.380514   73.315877   48.166215    6.039374  115.531124   77.997241   88.023412   43.083893   96.244094  117.313122  122.726607    32.79982         0.0         0.0        0.0        0.0     0.0  84.220758      19
eyeglasses_75_ICP           87.588102   87.952244  86.888912   44.465704  43.706854   46.803776   83.053832   86.934602  119.085669  118.664201  127.226752   89.041529   25.653662   76.212343  116.570636  110.974039  121.662971    92.39682   92.948404   45.527907         0.0         0.0        0.0        0.0     0.0  85.1679